In [1]:
import parastell
import logging
import csv
import numpy as np
#### THIS GETS THE SMOOTHED RADIAL DISTANCE FROM SOL TO COILS AT EACH PHI,
# THETA PAIR. IN THE DIRECTORY MUST EXIST A COILS STEP FILE NAME 'coils.step'
# additionally it is recommended that num_phi/phi_smooth step should be an integer
# likewise with theta


# Define number of toroidal cross-sections to make
num_phi = 80
# Define number of poloidal points to include in each toroidal cross-section
num_theta = 90
# Define the number of points to step over in the poloidal direction for smoothing
theta_smooth_step = 3
# Define the number of points to step over in the toroidal direction for smoothing
phi_smooth_step = 5

# Define plasma equilibrium VMEC file
plas_eq = 'plas_eq.nc'
# Define radial build
build = {
    'phi_list': np.linspace(0,90,num_phi),
    'theta_list': np.linspace(0,360, num_theta),
    'wall_s': 1.2,
    'radial_build': {
    }
}
# Define number of periods in stellarator plasma
num_periods = 4
# Define number of periods to generate
gen_periods = 1



# Define magnet coil parameters
magnets = {
    'file': 'coils.txt',
    'cross_section': ['circle', 20],
    'start': 3,
    'stop': None,
    'sample': 6,
    'name': 'magnet_coils',
    'h5m_tag': 'magnets',
    'meshing': False
}
# Define source mesh parameters
source = {
    'num_s': 11,
    'num_theta': 81,
    'num_phi': 241
}
# Define export parameters
export = {
    'exclude': [],
    'graveyard': False,
    'step_export': True,
    'h5m_export': None,
    'plas_h5m_tag': 'Vacuum',
    'sol_h5m_tag': 'Vacuum',
    # Note the following export parameters are used only for Cubit H5M exports
    'facet_tol': 1,
    'len_tol': 5,
    'norm_tol': None,
    # Note the following export parameters are used only for Gmsh H5M exports
    'min_mesh_size': 5.0,
    'max_mesh_size': 20.0,
    'volume_atol': 0.00001,
    'center_atol': 0.00001,
    'bounding_box_atol': 0.00001
}

# Define logger. Note that this is identical to the default logger instatiated
# by log.py. If no logger is passed to parametric_stellarator, this is the
# logger that will be used.
logger = logging.getLogger('log')
# Configure base logger message level
logger.setLevel(logging.INFO)
# Configure stream handler
s_handler = logging.StreamHandler()
# Configure file handler
f_handler = logging.FileHandler('stellarator.log')
# Define and set logging format
format = logging.Formatter(
    fmt = '%(asctime)s: %(message)s',
    datefmt = '%H:%M:%S'
)
s_handler.setFormatter(format)
f_handler.setFormatter(format)
# Add handlers to logger
logger.addHandler(s_handler)
logger.addHandler(f_handler)

# Create stellarator
strengths, point_list = parastell.parastell(
    plas_eq, num_periods, build, gen_periods, num_phi, num_theta,
    magnets = None, source = None, get_plasma_points = True,
    export = export, logger = logger
)

16:00:21: New stellarator build
16:00:21: Building plasma...
16:00:56: Building sol...
16:01:48: Exporting STEP files...



*******************************************************************
******        Statistics on Transfer (Write)                 ******

*******************************************************************
******        Transfer Mode = 0  I.E.  As Is       ******
******        Transferring Shape, ShapeType = 0                      ******
** WorkSession : Sending all data
 Step File Name : plasma.step(1209855 ents)  Write  Done

*******************************************************************
******        Statistics on Transfer (Write)                 ******

*******************************************************************
******        Transfer Mode = 0  I.E.  As Is       ******
******        Transferring Shape, ShapeType = 0                      ******
** WorkSession : Sending all data
 Step File Name : sol.step(2419676 ents)  Write  Done


In [2]:
# find available radial distance and apply smoothing algorithm
coil_path = 'magnet_coils.step'

radial_distances = parastell.get_radial_real_estate(point_list, coil_path, num_phi, num_theta)
radial_distances = parastell.smooth_torus(num_phi, num_theta, phi_smooth_step, theta_smooth_step, radial_distances, h=1, steps=25)



[2024-03-04 16:02:12.572] [info] Found python version 3 at /filespace/e/epflug/research/Coreform-Cubit-2023.11/bin/python3/libcubit_python3.so
[2024-03-04 16:02:12.572] [info] Looking for Python
[2024-03-04 16:02:12.576] [info] Version 3 interpreter found
[2024-03-04 16:02:12.623] [info] RLM session initialized


QObject::startTimer: Timers can only be used with threads started with QThread
QObject::startTimer: Timers can only be used with threads started with QThread
QObject::startTimer: Timers can only be used with threads started with QThread
QObject::startTimer: Timers can only be used with threads started with QThread
QObject::startTimer: Timers can only be used with threads started with QThread




                   CCCCC    UU   UU   BBBBBB    IIII   TTTTTT
                  CC   CC   UU   UU   BB   BB    II      TT
                  CC        UU   UU   BB   BB    II      TT
                  CC        UU   UU   BBBBBB     II      TT
                  CC        UU   UU   BB   BB    II      TT
                  CC   CC   UU   UU   BB   BB    II      TT
                   CCCCC     UUUUU    BBBBBB    IIII     TT  tm

                            MESH GENERATION TOOLKIT        
                                      FOR                   
                   PRE-PROCESSING OF FINITE ELEMENT ANALYSES

                User community forum: https://forum.coreform.com  


                         Cubit Version 2023.11 64-Bit Build b14f6c8f
                               VTK Version 9.2.2
                              ACIS Version 33.0.0.0
                            Exodus API Version 8.03
                            MeshGems Version 2.14-1
                     Copyright 2001-2019 Sand

/groupspace/cnerg/users/epflug/mambaforge/envs/parastell_env/lib/python3.11/site-packages/numpy/polynomial/polynomial.py:1362: RankWarning: The fit may be poorly conditioned
  return pu._fit(polyvander, x, y, deg, rcond, full, w)


In [4]:
#write out radial_distances to csv to avoid needing to recalculate it
with open('radial_distances.csv', 'w') as csvFile:
        csvwriter = csv.writer(csvFile)
        csvwriter.writerows(radial_distances)

In [5]:
#now make a build to check how it did
build = {
    'phi_list': np.linspace(0,90,num_phi),
    'theta_list': np.linspace(0,360, num_theta),
    'wall_s': 1.2,
    'radial_build': {
        'radial_distance':{
            'thickness_matrix': radial_distances-5 #minus a bit otherwise they
            # are tangent/overlap slightly in some locations
        }
    }
}

# this stellarator will have the sol, and one additional layer that
# represesnts the total thickness available there. Open that layer along
# with the magnet step file in cubit to visualize/check for overlap
# Create stellarator
strengths, point_list = parastell.parastell(
    plas_eq, num_periods, build, gen_periods, num_phi, num_theta,
    magnets = None, source = None, get_plasma_points = True,
    export = export, logger = logger
)

16:17:21: New stellarator build
16:17:21: Building plasma...
16:17:56: Building sol...
16:18:49: Building radial_distance...
16:20:18: Exporting STEP files...



*******************************************************************
******        Statistics on Transfer (Write)                 ******

*******************************************************************
******        Transfer Mode = 0  I.E.  As Is       ******
******        Transferring Shape, ShapeType = 0                      ******
** WorkSession : Sending all data
 Step File Name : plasma.step(1209855 ents)  Write  Done

*******************************************************************
******        Statistics on Transfer (Write)                 ******

*******************************************************************
******        Transfer Mode = 0  I.E.  As Is       ******
******        Transferring Shape, ShapeType = 0                      ******
** WorkSession : Sending all data
 Step File Name : sol.step(2419676 ents)  Write  Done

*******************************************************************
******        Statistics on Transfer (Write)                 ******

***